# This code uses the decoder to graph the pre-lesion phrase duration against the post-lesion phrase duration for bird (color-coded), with a point for each syllable type.

## Adjust lines 72 and 73 to be the path to the decoder output .json file and the creation data/parameters .json file that contains the treatment date.
### You will (eventually) need to have a folder of all of the Area X lesioned birds' decoders .csv in it.

### Step 0: Make a folder that has the .csv files from all of the Area X birds.

# Figure out the basic task first:

For now, load ONE .csv file, organize it into a dataframe. 

In [15]:
import json
import pandas as pd
import numpy as np
from datetime import datetime

class DecoderDataProcessor:
    def __init__(self, json_file_path, json_date_file_path):
        self.json_file_path = json_file_path
        self.json_date_file_path = json_date_file_path
        self.decoder_dataframe = self.load_data()
        self.subdirectory_dates = self.load_subdirectory_dates()

    def load_data(self):
        print(f"Reading JSON file: {self.json_file_path}")
        with open(self.json_file_path, 'r') as f:
            decoder_data = json.load(f)['results']
        return pd.DataFrame(decoder_data)

    def load_subdirectory_dates(self):
        with open(self.json_date_file_path, 'r') as f:
            json_data = json.load(f)
            subdirectory_dates = {subdir: datetime.strptime(data['subdirectory_creation_date'], "%Y-%m-%d").date() for subdir, data in json_data['subdirectories'].items()}
        return subdirectory_dates

    def parse_json_safe(self, s):
        if isinstance(s, dict):
            return s
        if pd.isna(s):
            return {}
        s = s.strip().strip("''")
        s = s.replace("'", '"')
        try:
            return json.loads(s)
        except json.JSONDecodeError:
            return {}

    def organize_data(self):
        self.decoder_dataframe['syllable_onsets_offsets_ms'] = self.decoder_dataframe['syllable_onsets_offsets_ms'].apply(self.parse_json_safe)
        self.decoder_dataframe['syllable_onsets_offsets_timebins'] = self.decoder_dataframe['syllable_onsets_offsets_timebins'].apply(self.parse_json_safe)
        
        self.decoder_dataframe = self.decoder_dataframe[self.decoder_dataframe['song_present'] == True].reset_index(drop=True)
        for i, row in self.decoder_dataframe.iterrows():
            file_name = row['file_name']
            animal_id, date_str, hour, minute, second = self.extract_date_time(file_name)
            self.decoder_dataframe.at[i, 'Animal ID'] = animal_id
            self.decoder_dataframe.at[i, 'Date'] = self.apply_year_correction(date_str)
            self.decoder_dataframe.at[i, 'Hour'] = hour
            self.decoder_dataframe.at[i, 'Minute'] = minute
            self.decoder_dataframe.at[i, 'Second'] = second
        self.decoder_dataframe['Date'] = pd.to_datetime(self.decoder_dataframe['Date'], format='%Y.%m.%d', errors='coerce')

    def extract_date_time(self, file_name):
        try:
            parts = file_name.split('_')
            return parts[0], f"{parts[2]}.{parts[3]}", parts[4], parts[5], parts[6].replace('.wav', '')
        except IndexError:
            return None, None, None, None, None

    def apply_year_correction(self, month_day):
        if month_day is None:
            return None
        try:
            month, day = month_day.split('.')
            for subdir, date in self.subdirectory_dates.items():
                if date.month == int(month) and date.day == int(day):
                    return date.strftime('%Y.%m.%d')
        except ValueError:
            return None
        return None

# Usage
json_file_path = '/Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_NOT_balanced_training_data/USA5271_decoded.json'
json_date_file_path = '/Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_NOT_balanced_training_data/USA5271_creation_data.json'
processor = DecoderDataProcessor(json_file_path, json_date_file_path)
processor.organize_data()
print(processor.decoder_dataframe.head(3))

Reading JSON file: /Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_NOT_balanced_training_data/USA5271_decoded.json
                                 file_name  song_present  \
0  USA5271_45342.27393766_2_20_7_36_33.wav          True   
1  USA5271_45342.27408656_2_20_7_36_48.wav          True   
2  USA5271_45342.27450617_2_20_7_37_30.wav          True   

                          syllable_onsets_offsets_ms  \
0  {'6': [[0.0, 291.42857142857144], [469.5238095...   
1  {'3': [[0.0, 40.47619047619048]], '20': [[40.4...   
2  {'6': [[0.0, 920.1587301587302], [1130.6349206...   

                    syllable_onsets_offsets_timebins Animal ID       Date  \
0  {'6': [[0.0, 108], [174.0, 217], [219.0, 220],...   USA5271 2024-02-20   
1  {'3': [[0.0, 15]], '20': [[15.000000000000002,...   USA5271 2024-02-20   
2  {'6': [[0.0, 341], [419.0, 1019], [1032.0, 107...   USA5271 2024-02-20   

  Hour Minute Second  
0    7     36     33  
1    7     36   

Find the treatment day and type.

In [16]:
import os
import json
# Load the JSON file and extract the treatment date
with open(json_date_file_path, 'r') as file:
    json_data = json.load(file)

#find the animal ID from the file name:
file_name = os.path.basename(json_date_file_path)
animal_id = file_name.split('_')[0]  # Assuming the ID is always the first part of the file name

# Extract and print the treatment date and type
treatment_date = json_data.get("treatment_date", "Treatment date not found")
treatment_type = json_data.get("treatment_type", "Treatment type not found")

print(f"Animal ID: {animal_id}")
print(f"Treatment Date: {treatment_date}")
print(f"Treatment Type: {treatment_type}")

Animal ID: USA5271
Treatment Date: 2024-03-07
Treatment Type: Sham lesion (saline)


Split up the data into pre-lesion and post-lesion data.

In [17]:
# Get data from one day
df = pd.DataFrame(processor.decoder_dataframe)
specific_date = pd.Timestamp('2024-03-19')

# Filter the DataFrame for rows where the Date column matches the specific date
filtered_df = df[df
['Date'] == specific_date]

# Select the syllable_onsets_offsets_ms column from the filtered DataFrame
syllable_onsets_offsets_ms_values = filtered_df['syllable_onsets_offsets_ms']
print(syllable_onsets_offsets_ms_values)

1879    {'6': [[0.0, 56.66666666666667], [706.98412698...
1880    {'20': [[0.0, 53.968253968253975], [148.412698...
1881    {'20': [[0.0, 37.77777777777778], [196.9841269...
1882    {'4': [[0.0, 48.57142857142858], [56.666666666...
1883    {'20': [[0.0, 183.4920634920635]], '6': [[183....
                              ...                        
1960    {'6': [[0.0, 16.19047619047619], [18.888888888...
1961    {'14': [[0.0, 5.396825396825397], [8.095238095...
1962    {'14': [[0.0, 534.2857142857143], [542.3809523...
1963    {'6': [[0.0, 161.90476190476193], [836.5079365...
1964    {'14': [[0.0, 8.095238095238095], [18.88888888...
Name: syllable_onsets_offsets_ms, Length: 86, dtype: object


Find all the unique syllable labels from TweetyBERT.

In [18]:
df = pd.DataFrame(processor.decoder_dataframe)

# Function to extract unique syllable labels from a DataFrame
def extract_unique_syllable_labels(df):
    unique_syllable_labels = set()
    for syllable_dict in df['syllable_onsets_offsets_ms']:
        if isinstance(syllable_dict, dict):
            unique_syllable_labels.update(syllable_dict.keys())
    return sorted(unique_syllable_labels)  # Return a sorted list of unique labels for easier viewing

# Extract and print unique syllable labels
unique_labels = extract_unique_syllable_labels(df)
print("Unique syllable labels:", unique_labels)


Unique syllable labels: ['0', '1', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '2', '20', '21', '22', '23', '25', '3', '4', '5', '6', '7', '8', '9']


Balance the datsets by figuring out which has the smallest sample size, then take an equivalent number of song from the second half of the pre-lesion data (and all data from the post-lesion dataset?)

In [19]:
# Assuming treatment_date is set as follows:
#treatment_date = pd.Timestamp('2024-04-09')

# Count rows before the treatment date
rows_before_treatment = df[df['Date'] < treatment_date].shape[0]
# Count rows after the treatment date
rows_after_treatment = df[df['Date'] > treatment_date].shape[0]
# Set song_sample_size to the smallest value between rows_before_treatment and rows_after_treatment
song_sample_size = min(rows_before_treatment, rows_after_treatment)

print("Song sample size:", song_sample_size)

# Filter the DataFrame for rows before the treatment date and sort by Date descending to get the latest data
pre_treatment = df[df['Date'] < treatment_date].sort_values(by='Date', ascending=False).head(song_sample_size)

# Filter the DataFrame for rows after the treatment date and sort by Date ascending to get the earliest data
post_treatment = df[df['Date'] > treatment_date].sort_values(by='Date', ascending=True).head(song_sample_size)

# Display the result
print("Pre-treatment data:", pre_treatment.head(3))
print("Post-treatment data:", post_treatment)

# If you want to print just the 'syllable_onsets_offsets_ms' column from the post-treatment data
#print("Post-treatment 'syllable_onsets_offsets_ms' data:\n", pre_treatment['syllable_onsets_offsets_ms'][13142])
# If you also want to include the file_name column or other identifying information, you could do:
#print("Post-treatment data including file names and syllable onsets/offsets:\n", post_treatment[['file_name', 'syllable_onsets_offsets_ms']])


Song sample size: 2466
Pre-treatment data:                                    file_name  song_present  \
1233  USA5271_45357.28231355_3_6_7_50_31.wav          True   
1211   USA5271_45357.27308179_3_6_7_35_8.wav          True   
1209  USA5271_45357.27237449_3_6_7_33_57.wav          True   

                             syllable_onsets_offsets_ms  \
1233  {'6': [[0.0, 261.74603174603175], [313.0158730...   
1211  {'6': [[0.0, 1632.5396825396826]], '3': [[1632...   
1209  {'6': [[0.0, 1721.5873015873017], [2463.650793...   

                       syllable_onsets_offsets_timebins Animal ID       Date  \
1233  {'6': [[0.0, 97], [115.99999999999999, 209], [...   USA5271 2024-03-06   
1211           {'6': [[0.0, 605]], '3': [[605.0, 650]]}   USA5271 2024-03-06   
1209  {'6': [[0.0, 638], [913.0, 1065], [1375.0, 223...   USA5271 2024-03-06   

     Hour Minute Second  
1233    7     50     31  
1211    7     35      8  
1209    7     33     57  
Post-treatment data:                          

For one syllable type, find all the onset and offset values. I'll choose '26', since it shows up with more than one onset/offset interval, so I can make sure the code checks all of the intervals for durations.

In [20]:
# import pandas as pd
# import ast  # Import Abstract Syntax Trees to safely evaluate strings containing Python literals

# # Function to calculate durations for syllable '26'
# def calculate_durations(df):
#     durations = []
#     for index, row in df.iterrows():
#         syllable_data = row['syllable_onsets_offsets_ms']
#         if '26' in syllable_data:
#             for interval in syllable_data['26']:
#                 duration = interval[1] - interval[0]
#                 durations.append(duration)
#     return durations

# # Calculate durations for syllable '26' in the pre-treatment data
# syllable_26_durations_pre_treatment = calculate_durations(pre_treatment)
# print("Syllable '26' durations (pre-treatment):", syllable_26_durations_pre_treatment)


Now, get it to iterate over all the unique syllable labels that you found from the unique_labels array:

In [21]:
# import pandas as pd
# import ast  # Import Abstract Syntax Trees to safely evaluate strings containing Python literals

# # Function to calculate durations for a specified syllable type
# def calculate_durations(df, syllable_type):
#     durations = []
#     for index, row in df.iterrows():
#         syllable_data = ast.literal_eval(row['syllable_onsets_offsets_ms'])
#         if syllable_type in syllable_data:
#             for interval in syllable_data[syllable_type]:
#                 duration = interval[1] - interval[0]
               


In [22]:
import pandas as pd
import ast  # Import Abstract Syntax Trees to safely evaluate strings containing Python literals

# Function to calculate durations for each syllable type
def calculate_durations(df, syllable_labels):
    durations_dict = {label: [] for label in syllable_labels}  # Initialize a dictionary to store durations for each label
    for index, row in df.iterrows():
        syllable_data = row['syllable_onsets_offsets_ms']
        for label in syllable_labels:
            if label in syllable_data:
                for interval in syllable_data[label]:
                    duration = interval[1] - interval[0]  # Calculate duration
                    durations_dict[label].append(duration)  # Append duration to the corresponding list
    return durations_dict

# Calculate durations for all syllable types in the pre-treatment data
syllable_durations_pre_treatment = calculate_durations(pre_treatment, unique_labels)
# Calculate durations for all syllable types in the post-treatment data
syllable_durations_post_treatment = calculate_durations(post_treatment, unique_labels)

# Convert the dictionary to a DataFrame for pre-treatment data
max_length_pre = max(len(v) for v in syllable_durations_pre_treatment.values())
df_durations_pre = pd.DataFrame({k: pd.Series(v) for k, v in syllable_durations_pre_treatment.items()}, index=range(max_length_pre))

# Convert the dictionary to a DataFrame for post-treatment data
max_length_post = max(len(v) for v in syllable_durations_post_treatment.values())
df_durations_post = pd.DataFrame({k: pd.Series(v) for k, v in syllable_durations_post_treatment.items()}, index=range(max_length_post))

# Display the DataFrames
print("Pre-treatment Durations DataFrame:")
print(df_durations_pre)

#print("\nPost-treatment Durations DataFrame:")
#print(df_durations_post.head(2))

# Save the pre-treatment durations DataFrame as a CSV file on the desktop
df_durations_pre.to_csv('/Users/mirandahulsey-vincent/Desktop/pre_treatment_durations.csv', index=False)

# Save the post-treatment durations DataFrame as a CSV file on the desktop
df_durations_post.to_csv('/Users/mirandahulsey-vincent/Desktop/post_treatment_durations.csv', index=False)

print("CSV files have been saved to your desktop.")



Pre-treatment Durations DataFrame:
               0          1          10        11          12         13  \
0      16.190476  24.285714   37.777778  5.396825   26.984127   5.396825   
1      37.777778   5.396825    2.698413       NaN  151.111111  10.793651   
2      16.190476   8.095238  366.984127       NaN    5.396825  45.873016   
3      78.253968   2.698413  226.666667       NaN    2.698413  40.476190   
4      83.650794   8.095238    2.698413       NaN    2.698413  35.079365   
...          ...        ...         ...       ...         ...        ...   
40629        NaN        NaN         NaN       NaN         NaN        NaN   
40630        NaN        NaN         NaN       NaN         NaN        NaN   
40631        NaN        NaN         NaN       NaN         NaN        NaN   
40632        NaN        NaN         NaN       NaN         NaN        NaN   
40633        NaN        NaN         NaN       NaN         NaN        NaN   

               14   15         16   17  ...         

In [23]:
import pandas as pd
import ast  # Import Abstract Syntax Trees to safely evaluate strings containing Python literals

# Function to calculate durations for each syllable type, including file_name
def calculate_durations_with_filename(df, syllable_labels):
    rows = []  # This list will store a dictionary for each syllable occurrence
    for index, row in df.iterrows():
        file_name = row['file_name']  # Assumes that your DataFrame has a 'file_name' column
        syllable_data = row['syllable_onsets_offsets_ms']
        for label in syllable_labels:
            if label in syllable_data:
                for interval in syllable_data[label]:
                    duration = interval[1] - interval[0]  # Calculate duration
                    # Append a row with file_name, syllable label, and duration
                    rows.append({
                        'file_name': file_name,
                        'syllable': label,
                        'duration': duration
                    })
    return pd.DataFrame(rows)

# Calculate durations DataFrame for pre-treatment data (includes file_name)
df_durations_pre = calculate_durations_with_filename(pre_treatment, unique_labels)
# Calculate durations DataFrame for post-treatment data (includes file_name)
df_durations_post = calculate_durations_with_filename(post_treatment, unique_labels)

# Display a preview of the DataFrames
print("Pre-treatment Durations DataFrame (first 5 rows):")
print(df_durations_pre.head())

print("\nPost-treatment Durations DataFrame (first 5 rows):")
print(df_durations_post.head())

# Save the pre-treatment durations DataFrame as a CSV file on the desktop
df_durations_pre.to_csv('/Users/mirandahulsey-vincent/Desktop/pre_treatment_durations.csv', index=False)

# Save the post-treatment durations DataFrame as a CSV file on the desktop
df_durations_post.to_csv('/Users/mirandahulsey-vincent/Desktop/post_treatment_durations.csv', index=False)

print("CSV files have been saved to your desktop.")


Pre-treatment Durations DataFrame (first 5 rows):
                                file_name syllable    duration
0  USA5271_45357.28231355_3_6_7_50_31.wav       14   26.984127
1  USA5271_45357.28231355_3_6_7_50_31.wav       14  272.539683
2  USA5271_45357.28231355_3_6_7_50_31.wav        3  172.698413
3  USA5271_45357.28231355_3_6_7_50_31.wav        4    2.698413
4  USA5271_45357.28231355_3_6_7_50_31.wav        6  261.746032

Post-treatment Durations DataFrame (first 5 rows):
                                 file_name syllable    duration
0  USA5271_45360.45288362_3_9_12_34_48.wav        3   59.365079
1  USA5271_45360.45288362_3_9_12_34_48.wav        3   10.793651
2  USA5271_45360.45288362_3_9_12_34_48.wav        3  313.015873
3  USA5271_45360.45288362_3_9_12_34_48.wav        3    2.698413
4  USA5271_45360.45288362_3_9_12_34_48.wav        3   13.492063
CSV files have been saved to your desktop.


Next, find the mean, SEM, median, standard  deviation, and variance of each syllable's phrase duration.

In [24]:
import pandas as pd
import numpy as np

# Function to calculate statistics for each syllable type in a given DataFrame
def calculate_statistics(df):
    # Dictionary to hold the statistics for each syllable
    stats_dict = {}
    
    # Iterate through each syllable column in the DataFrame
    for column in df:
        # Drop NaN values for accurate statistics
        data = df[column].dropna()
        
        # Calculate required statistics
        mean = data.mean()
        sem = data.sem()
        median = data.median()
        std_dev = data.std()
        variance = data.var()
        
        # Store the statistics in the dictionary
        stats_dict[column] = {
            'Mean': mean,
            'SEM': sem,
            'Median': median,
            'Standard Deviation': std_dev,
            'Variance': variance
        }
        
    return stats_dict

# Calculate statistics for pre-treatment and post-treatment DataFrames
stats_pre_treatment = calculate_statistics(df_durations_pre)
stats_post_treatment = calculate_statistics(df_durations_post)

# Optionally, convert these dictionaries to DataFrames for better visualization
df_stats_pre_treatment = pd.DataFrame(stats_pre_treatment).T
df_stats_post_treatment = pd.DataFrame(stats_post_treatment).T

# Display the statistics DataFrames
print("Pre-treatment Syllable Duration Statistics:")
print(df_stats_pre_treatment.head(2))
print("\nPost-treatment Syllable Duration Statistics:")
print(df_stats_post_treatment.head(2))


TypeError: Could not convert string 'USA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.28231355_3_6_7_50_31.wavUSA5271_45357.27308179_3_6_7_35_8.wavUSA5271_45357.27308179_3_6_7_35_8.wavUSA5271_45357.27237449_3_6_7_33_57.wavUSA5271_45357.27237449_3_6_7_33_57.wavUSA5271_45357.27237449_3_6_7_33_57.wavUSA5271_45357.27237449_3_6_7_33_57.wavUSA5271_45357.27237449_3_6_7_33_57.wavUSA5271_45357.27237449_3_6_7_33_57.wavUSA5271_45357.27237449_3_6_7_33_57.wavUSA5271_45357.27237449_3_6_7_33_57.wavUSA5271_45357.27237449_3_6_7_33_57.wavUSA5271_45357.27237449_3_6_7_33_57.wavUSA5271_45357.27237449_3_6_7_33_57.wavUSA5271_45357.2

Plot the pre-treatment and post-treatment mean average, median average, and variance for each syllable.

In [10]:
# import matplotlib.pyplot as plt

# # Extract mean values for each syllable from the statistics DataFrames
# mean_pre_treatment = df_stats_pre_treatment['Mean']
# mean_post_treatment = df_stats_post_treatment['Mean']

# # Create a scatter plot
# fig, ax = plt.subplots(figsize=(8, 8))  # Smaller figure size
# ax.scatter(mean_pre_treatment, mean_post_treatment, color='b', alpha=0.5)

# # Adding labels and title with increased font size and including animal_id
# ax.set_xlabel('Pre-treatment Mean Phrase Durations (ms)', fontsize=18)
# ax.set_ylabel('Post-treatment Mean Phrase Durations (ms)', fontsize=18)
# ax.set_title(f'{animal_id} Mean Phrase Durations \n treatment date {treatment_date}, sample size = {song_sample_size} songs', fontsize=24)

# # Adding a reference line to indicate no change
# ax.plot([min(mean_pre_treatment.min(), mean_post_treatment.min()), max(mean_pre_treatment.max(), mean_post_treatment.max())],
#         [min(mean_pre_treatment.min(), mean_post_treatment.min()), max(mean_pre_treatment.max(), mean_post_treatment.max())],
#         'r--', label='y=x')

# ax.legend(fontsize=24, loc = 'lower right')
# ax.tick_params(axis='both', which='major', labelsize=20)

# # Remove gridlines
# ax.grid(False)

# # Remove top and right spines
# ax.spines['top'].set_visible(False)
# ax.spines['right'].set_visible(False)

# # Display the plot
# plt.show()


In [11]:
# import matplotlib.pyplot as plt
# import pandas as pd

# df_stats_pre_treatment = pd.DataFrame(df_stats_pre_treatment)
# df_stats_post_treatment = pd.DataFrame(df_stats_post_treatment)

# # Extract mean values for plotting
# mean_pre_treatment = df_stats_pre_treatment['Mean']
# mean_post_treatment = df_stats_post_treatment['Mean']

# # Create a scatter plot
# plt.figure(figsize=(10, 8))
# plt.scatter(mean_pre_treatment, mean_post_treatment, color='blue')

# # Adding a red dashed line for y=x
# max_value = max(max(mean_pre_treatment), max(mean_post_treatment))
# plt.plot([0, max_value], [0, max_value], 'r--', label='y=x')

# # Annotating each point with its syllable label (0, 1, ..., n-1)
# for i, (x, y) in enumerate(zip(mean_pre_treatment, mean_post_treatment)):
#     plt.annotate(i, (x, y), textcoords="offset points", xytext=(0,10), ha='center')

# # Adding plot labels and title
# plt.xlabel('Pre-Treatment Mean Durations (ms)', fontsize = 16)
# plt.ylabel('Post-Treatment Mean Durations (ms)', fontsize = 16)
# plt.title(f'{animal_id} Mean Phrase Durations \n treatment date {treatment_date}, sample size = {song_sample_size} songs', fontsize=16)
# # Remove spines & show legend
# ax = plt.gca()  # Get current axes
# ax.spines['top'].set_visible(False)
# ax.spines['right'].set_visible(False)
# plt.legend()
# plt.show()


In [12]:
import matplotlib.pyplot as plt
import pandas as pd

# Assuming df_stats_pre_treatment and df_stats_post_treatment are already defined DataFrames

# Extract values for plotting
mean_pre_treatment = df_stats_pre_treatment['Mean']
mean_post_treatment = df_stats_post_treatment['Mean']
median_pre_treatment = df_stats_pre_treatment['Median']
median_post_treatment = df_stats_post_treatment['Median']
variance_pre_treatment = df_stats_pre_treatment['Variance']
variance_post_treatment = df_stats_post_treatment['Variance']

# Create a figure with subplots
fig, axs = plt.subplots(1, 3, figsize=(27, 8))  # 1 row, 3 columns

# Define a function to plot data and annotations
def plot_data(ax, x_data, y_data, title, x_label, y_label, color):
    ax.scatter(x_data, y_data, color=color)
    ax.plot([0, max(max(x_data), max(y_data))], [0, max(max(x_data), max(y_data))], 'r--', label='y=x')
    ax.set_xlabel(x_label, fontsize=16)
    ax.set_ylabel(y_label, fontsize=16)
    ax.set_title(title, fontsize=16)
    ax.legend()
    ax.spines['top'].set_visible(False)
    ax.spines['right'].set_visible(False)
    # Adding annotations for each point
    for i, (x, y) in enumerate(zip(x_data, y_data)):
        ax.annotate(f'S{i}', (x, y), textcoords="offset points", xytext=(0,10), ha='center')

# Plotting Means
plot_data(axs[0], mean_pre_treatment, mean_post_treatment, 'Mean Phrase Durations', 'Pre-Treatment (ms)', 'Post-Treatment (ms)', 'blue')

# Plotting Medians
plot_data(axs[1], median_pre_treatment, median_post_treatment, 'Median Phrase Durations', 'Pre-Treatment (ms)', 'Post-Treatment (ms)', 'green')

# Plotting Variances
plot_data(axs[2], variance_pre_treatment, variance_post_treatment, 'Variance of Phrase Durations', 'Pre-Treatment (ms²)', 'Post-Treatment (ms²)', 'black')

# Set the overall title for the figure
fig.suptitle(f'{animal_id} Phrase Durations\nTreatment Date: {treatment_date}, Sample Size: {song_sample_size} songs', fontsize=18, fontweight='bold')

# Adjust subplot layout
plt.tight_layout(rect=[0, 0.03, 1, 0.95])  # Adjust the rect to make space for the suptitle

# Display the plot
plt.show()


In [13]:
import matplotlib.pyplot as plt
import pandas as pd

# Assuming df_stats_pre_treatment and df_stats_post_treatment are already defined DataFrames

# Extract values for plotting
mean_pre_treatment = df_stats_pre_treatment['Mean']
mean_post_treatment = df_stats_post_treatment['Mean']
median_pre_treatment = df_stats_pre_treatment['Median']
median_post_treatment = df_stats_post_treatment['Median']
variance_pre_treatment = df_stats_pre_treatment['Variance']
variance_post_treatment = df_stats_post_treatment['Variance']

# Create a figure with subplots
fig, axs = plt.subplots(1, 3, figsize=(30, 10))  # 1 row, 3 columns

# Define a function to plot data and annotations
import numpy as np

# Define a function to plot data and annotations, including NaN and Inf handling
def plot_data(ax, x_data, y_data, title, x_label, y_label, color):
    # Handle NaNs or Infs in the data
    mask = np.isfinite(x_data) & np.isfinite(y_data)
    x_data = x_data[mask]
    y_data = y_data[mask]

    ax.scatter(x_data, y_data, color=color)
    # Set limits based on the valid data
    if len(x_data) > 0 and len(y_data) > 0:  # Check if there's any data left after removing NaNs/Infs
        lims = [
            min(min(x_data), min(y_data)),  # minimum of data
            max(max(x_data+100), max(y_data+100))   # maximum of data
        ]
        ax.plot(lims, lims, 'r--', label='y=x')
        ax.set_xlim(lims)
        ax.set_ylim(lims)
    else:
        ax.plot([], [], 'r--', label='y=x')  # Plot an empty line with the label

    ax.set_xlabel(x_label, fontsize=24)
    ax.set_ylabel(y_label, fontsize=24)
    ax.set_title(title, fontsize=24)
    ax.legend()
    ax.spines['top'].set_visible(False)
    ax.spines['right'].set_visible(False)
    # Adding annotations for each point
    for i, (x, y) in enumerate(zip(x_data, y_data)):
        ax.annotate(f'S{i}', (x, y), textcoords="offset points", xytext=(0,10), ha='center')

# Usage of the function remains the same, ensuring data passed into it is cleaned


# Plotting Means
plot_data(axs[0], mean_pre_treatment, mean_post_treatment, 'Mean Phrase Durations', 'Pre-Treatment (ms)', 'Post-Treatment (ms)', 'blue')

# Plotting Medians
plot_data(axs[1], median_pre_treatment, median_post_treatment, 'Median Phrase Durations', 'Pre-Treatment (ms)', 'Post-Treatment (ms)', 'green')

# Plotting Variances
plot_data(axs[2], variance_pre_treatment, variance_post_treatment, 'Variance of Phrase Durations', 'Pre-Treatment (ms²)', 'Post-Treatment (ms²)', 'black')

# Set the overall title for the figure
fig.suptitle(f'{animal_id} Phrase Durations\nTreatment Date: {treatment_date}, Sample Size: {song_sample_size} songs', fontsize=24, fontweight='bold')

# Adjust subplot layout
plt.tight_layout(rect=[0, 0.03, 1, 0.95])  # Adjust the rect to make space for the suptitle

# Display the plot
plt.show()


# Another approach: get it to save as a .csv file, then later I'll combine them and graph them all together.

In [14]:
# Combining the data into a new DataFrame
combined_data = pd.DataFrame({
    'Mean_Pre_Treatment': mean_pre_treatment,
    'Mean_Post_Treatment': mean_post_treatment,
    'Median_Pre_Treatment': median_pre_treatment,
    'Median_Post_Treatment': median_post_treatment,
    'Variance_Pre_Treatment': variance_pre_treatment,
    'Variance_Post_Treatment': variance_post_treatment
})

# Adding the animal_id as the first column of the DataFrame
combined_data.insert(0, 'Animal_ID', animal_id)

# Extract the directory from the provided JSON file path
directory = os.path.dirname(json_file_path)

# Save to CSV in the same directory as the JSON file
combined_data.to_csv(os.path.join(directory, f'{animal_id}_treatment_comparison.csv'), index=False)


# Working on code that repeats for ALL the files in a given folder

In [15]:
# import os
# from collections import defaultdict

# def find_matching_json_files(directory):
#     files_by_animal = defaultdict(list)
#     # Walk through the directory and subdirectories
#     for root, dirs, files in os.walk(directory):
#         for file in files:
#             if file.endswith('.json'):
#                 # Extract the animal ID by splitting the filename at the first underscore
#                 animal_id = file.split('_', 1)[0]
#                 files_by_animal[animal_id].append(os.path.join(root, file))

#     # Filter out entries with less than 2 files
#     matching_files = {animal_id: paths for animal_id, paths in files_by_animal.items() if len(paths) == 2}
#     return matching_files

# # Example usage:
# folder_path = '/Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files'
# matching_files = find_matching_json_files(folder_path)
# print("Matching JSON files by animal ID:")
# for animal_id, files in matching_files.items():
#     print(f"{animal_id}: {files}")


In [16]:
# import os
# from collections import defaultdict

# def find_matching_json_files(directory):
#     files_by_animal = defaultdict(list)
#     # Walk through the directory and subdirectories
#     for root, dirs, files in os.walk(directory):
#         for file in files:
#             if file.endswith('.json'):
#                 # Extract the animal ID by splitting the filename at the first underscore
#                 animal_id = file.split('_', 1)[0]
#                 files_by_animal[animal_id].append(os.path.join(root, file))

#     # Organize files by their specific roles
#     organized_files = {}
#     for animal_id, file_paths in files_by_animal.items():
#         decoded_file = None
#         creation_file = None
#         for file_path in file_paths:
#             if 'decoded_database' in file_path:
#                 decoded_file = file_path
#             elif 'creation_data' in file_path:
#                 creation_file = file_path
#         if decoded_file and creation_file:
#             organized_files[animal_id] = {'decoded_database': decoded_file, 'creation_data': creation_file}

#     return organized_files

# # Example usage:
# folder_path = '/Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files'
# matching_files = find_matching_json_files(folder_path)
# print("Organized JSON files by animal ID:")
# for animal_id, files in matching_files.items():
#     print(f"{animal_id}: Decoded: {files['decoded_database']}, Creation: {files['creation_data']}")


In [17]:
import os
import json
import pandas as pd
from datetime import datetime
from collections import defaultdict

class DecoderDataProcessor:
    def __init__(self, json_file_path, json_date_file_path):
        self.json_file_path = json_file_path
        self.json_date_file_path = json_date_file_path
        self.decoder_dataframe = self.load_data()
        self.subdirectory_dates = self.load_subdirectory_dates()

    def load_data(self):
        print(f"Reading JSON file: {self.json_file_path}")
        with open(self.json_file_path, 'r') as f:
            decoder_data = json.load(f)['results']
        return pd.DataFrame(decoder_data)

    def load_subdirectory_dates(self):
        print(f"Reading JSON date file: {self.json_date_file_path}")
        with open(self.json_date_file_path, 'r') as f:
            json_data = json.load(f)
            subdirectory_dates = {subdir: datetime.strptime(data['subdirectory_creation_date'], "%Y-%m-%d").date() for subdir, data in json_data['subdirectories'].items()}
        return subdirectory_dates

    def organize_data(self):
        # Add the data organization logic as required
        pass

def find_matching_json_files(directory):
    files_by_animal = defaultdict(list)
    for root, dirs, files in os.walk(directory):
        for file in files:
            if file.endswith('.json'):
                animal_id = file.split('_', 1)[0]
                files_by_animal[animal_id].append(os.path.join(root, file))

    organized_files = {}
    for animal_id, file_paths in files_by_animal.items():
        decoded_file = None
        creation_file = None
        for file_path in file_paths:
            if 'decoded_database' in file_path:
                decoded_file = file_path
            elif 'creation_data' in file_path:
                creation_file = file_path
        if decoded_file and creation_file:
            organized_files[animal_id] = {'decoded_database': decoded_file, 'creation_data': creation_file}

    return organized_files

def process_files(directory):
    animal_files = find_matching_json_files(directory)
    for animal_id, files in animal_files.items():
        processor = DecoderDataProcessor(files['decoded_database'], files['creation_data'])
        processor.organize_data()
        print(f"Data for Animal ID: {animal_id}")
        print(processor.decoder_dataframe.head(3))

# Example usage:
directory = '/Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files'
process_files(directory)


Reading JSON file: /Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files/USA5509_decoded_database.json
Reading JSON date file: /Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files/USA5509_creation_data.json
Data for Animal ID: USA5509
                                  file_name  song_present  \
0  USA5509_45393.52552124_4_11_14_35_52.wav         False   
1   USA5509_45393.52741283_4_11_14_39_1.wav         False   
2   USA5509_45393.52749832_4_11_14_39_9.wav         False   

  syllable_onsets_offsets_ms syllable_onsets_offsets_timebins  
0                         {}                               {}  
1                         {}                               {}  
2                         {}                               {}  
Reading JSON file: /Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Are

In [18]:
import os
import json
import pandas as pd
from datetime import datetime
from collections import defaultdict

class DecoderDataProcessor:
    def __init__(self, json_file_path, json_date_file_path):
        self.json_file_path = json_file_path
        self.json_date_file_path = json_date_file_path
        self.decoder_dataframe = self.load_data()
        self.subdirectory_dates = self.load_subdirectory_dates()
        self.treatment_date, self.treatment_type = self.load_treatment_details()

    def load_data(self):
        print(f"Reading JSON file: {self.json_file_path}")
        with open(self.json_file_path, 'r') as f:
            decoder_data = json.load(f)['results']
        return pd.DataFrame(decoder_data)

    def load_subdirectory_dates(self):
        print(f"Reading JSON date file: {self.json_date_file_path}")
        with open(self.json_date_file_path, 'r') as f:
            json_data = json.load(f)
            subdirectory_dates = {subdir: datetime.strptime(data['subdirectory_creation_date'], "%Y-%m-%d").date() for subdir, data in json_data['subdirectories'].items()}
        return subdirectory_dates

    def load_treatment_details(self):
        print(f"Reading treatment details from: {self.json_date_file_path}")
        with open(self.json_date_file_path, 'r') as f:
            json_data = json.load(f)
        treatment_date = json_data.get("treatment_date", "Treatment date not found")
        treatment_type = json_data.get("treatment_type", "Treatment type not found")
        return treatment_date, treatment_type

    def organize_data(self):
        # Implement the existing logic to organize data
        pass

def find_matching_json_files(directory):
    files_by_animal = defaultdict(list)
    for root, dirs, files in os.walk(directory):
        for file in files:
            if file.endswith('.json'):
                animal_id = file.split('_', 1)[0]
                files_by_animal[animal_id].append(os.path.join(root, file))

    organized_files = {}
    for animal_id, file_paths in files_by_animal.items():
        decoded_file = None
        creation_file = None
        for file_path in file_paths:
            if 'decoded_database' in file_path:
                decoded_file = file_path
            elif 'creation_data' in file_path:
                creation_file = file_path
        if decoded_file and creation_file:
            organized_files[animal_id] = {'decoded_database': decoded_file, 'creation_data': creation_file}

    return organized_files

def process_files(directory):
    animal_files = find_matching_json_files(directory)
    for animal_id, files in animal_files.items():
        processor = DecoderDataProcessor(files['decoded_database'], files['creation_data'])
        processor.organize_data()
        print(f"Data for Animal ID: {animal_id}")
        print(f"Treatment Date: {processor.treatment_date}")
        print(f"Treatment Type: {processor.treatment_type}")
        print(processor.decoder_dataframe.head(3))

# Example usage:
directory = '/Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files'
process_files(directory)


Reading JSON file: /Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files/USA5509_decoded_database.json
Reading JSON date file: /Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files/USA5509_creation_data.json
Reading treatment details from: /Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files/USA5509_creation_data.json
Data for Animal ID: USA5509
Treatment Date: 2024-05-01
Treatment Type: Bilateral Area X lesion
                                  file_name  song_present  \
0  USA5509_45393.52552124_4_11_14_35_52.wav         False   
1   USA5509_45393.52741283_4_11_14_39_1.wav         False   
2   USA5509_45393.52749832_4_11_14_39_9.wav         False   

  syllable_onsets_offsets_ms syllable_onsets_offsets_timebins  
0                         {}       

In [19]:
import os
import json
import pandas as pd
from datetime import datetime
from collections import defaultdict

class DecoderDataProcessor:
    def __init__(self, json_file_path, json_date_file_path):
        self.json_file_path = json_file_path
        self.json_date_file_path = json_date_file_path
        self.decoder_dataframe = self.load_data()
        self.subdirectory_dates = self.load_subdirectory_dates()
        self.treatment_date, self.treatment_type = self.load_treatment_details()
        self.unique_syllable_labels = []

    def load_data(self):
        print(f"Reading JSON file: {self.json_file_path}")
        with open(self.json_file_path, 'r') as f:
            decoder_data = json.load(f)['results']
        return pd.DataFrame(decoder_data)

    def load_subdirectory_dates(self):
        print(f"Reading JSON date file: {self.json_date_file_path}")
        with open(self.json_date_file_path, 'r') as f:
            json_data = json.load(f)
            subdirectory_dates = {subdir: datetime.strptime(data['subdirectory_creation_date'], "%Y-%m-%d").date() for subdir, data in json_data['subdirectories'].items()}
        return subdirectory_dates

    def load_treatment_details(self):
        print(f"Reading treatment details from: {self.json_date_file_path}")
        with open(self.json_date_file_path, 'r') as f:
            json_data = json.load(f)
        treatment_date = json_data.get("treatment_date", "Treatment date not found")
        treatment_type = json_data.get("treatment_type", "Treatment type not found")
        return treatment_date, treatment_type

    def organize_data(self):
        # Implement the existing logic to organize data
        self.extract_unique_syllable_labels()

    def extract_unique_syllable_labels(self):
        unique_syllable_labels = set()
        for syllable_dict in self.decoder_dataframe['syllable_onsets_offsets_ms']:
            if isinstance(syllable_dict, dict):
                unique_syllable_labels.update(syllable_dict.keys())
        self.unique_syllable_labels = sorted(unique_syllable_labels)  # Store sorted list of unique labels

def find_matching_json_files(directory):
    files_by_animal = defaultdict(list)
    for root, dirs, files in os.walk(directory):
        for file in files:
            if file.endswith('.json'):
                animal_id = file.split('_', 1)[0]
                files_by_animal[animal_id].append(os.path.join(root, file))

    organized_files = {}
    for animal_id, file_paths in files_by_animal.items():
        decoded_file = None
        creation_file = None
        for file_path in file_paths:
            if 'decoded_database' in file_path:
                decoded_file = file_path
            elif 'creation_data' in file_path:
                creation_file = file_path
        if decoded_file and creation_file:
            organized_files[animal_id] = {'decoded_database': decoded_file, 'creation_data': creation_file}

    return organized_files

def process_files(directory):
    animal_files = find_matching_json_files(directory)
    for animal_id, files in animal_files.items():
        processor = DecoderDataProcessor(files['decoded_database'], files['creation_data'])
        processor.organize_data()
        print(f"Data for Animal ID: {animal_id}")
        print(f"Treatment Date: {processor.treatment_date}")
        print(f"Treatment Type: {processor.treatment_type}")
        print(f"Unique Syllable Labels: {processor.unique_syllable_labels}")
        print(processor.decoder_dataframe.head(3))

# Example usage:
directory = '/Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files'
process_files(directory)


Reading JSON file: /Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files/USA5509_decoded_database.json
Reading JSON date file: /Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files/USA5509_creation_data.json
Reading treatment details from: /Users/mirandahulsey-vincent/Documents/allPythonCode/syntax_analysis/data_inputs/Area_X_lesions_balanced_training_data/all_json_files/USA5509_creation_data.json
Data for Animal ID: USA5509
Treatment Date: 2024-05-01
Treatment Type: Bilateral Area X lesion
Unique Syllable Labels: ['0', '1', '10', '11', '12', '14', '15', '16', '2', '3', '4', '5', '6', '7', '8']
                                  file_name  song_present  \
0  USA5509_45393.52552124_4_11_14_35_52.wav         False   
1   USA5509_45393.52741283_4_11_14_39_1.wav         False   
2   USA5509_45393.52749832_4_11_14_39_9.wav         Fal